In [1]:
import pandas as pd
pd.set_option('display.max_columns', None)
import numpy as np
import matplotlib.pyplot as plt
from tqdm import tqdm
from sklearn.preprocessing import FunctionTransformer
import pickle
from typing import Dict



import plotly.graph_objects as go
import plotly.express as px
import plotly.subplots as sp

from tqdm import tqdm
from sklearn.preprocessing import FunctionTransformer
from sklearn.pipeline import make_pipeline
from sklego.preprocessing import RepeatingBasisFunction

import seaborn as sns
from datetime import datetime
from datetime import date
from datetime import timedelta

import holidays
import yaml

import torch
from torch import nn
from pytorch_forecasting import Baseline, TemporalFusionTransformer, TimeSeriesDataSet
from pytorch_forecasting.data import GroupNormalizer
from pytorch_forecasting.metrics import MAE, SMAPE, PoissonLoss, QuantileLoss, MultiLoss, CrossEntropy
from pytorch_forecasting.models.temporal_fusion_transformer.tuning import optimize_hyperparameters
from pytorch_forecasting.data.encoders import NaNLabelEncoder, MultiNormalizer, EncoderNormalizer, TorchNormalizer
from lightning.pytorch.utilities.model_summary import ModelSummary
from pytorch_forecasting.models import BaseModel
import lightning.pytorch as pl
from lightning.pytorch.callbacks import EarlyStopping, LearningRateMonitor
from lightning.pytorch.loggers import TensorBoardLogger

import statsmodels.api as sm
from statsmodels.tsa.stattools import adfuller

from imblearn.over_sampling import SMOTE
from imblearn.under_sampling import RandomUnderSampler, TomekLinks, NeighbourhoodCleaningRule
from sklearn.model_selection import  StratifiedShuffleSplit
from sklearn.preprocessing import  OneHotEncoder, FunctionTransformer, StandardScaler, OrdinalEncoder
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from sklearn.utils import class_weight
from sklearn.experimental import enable_iterative_imputer
from sklearn.impute import IterativeImputer, SimpleImputer
from sklearn.linear_model import BayesianRidge
from sklearn.ensemble import  HistGradientBoostingRegressor

Read the Parquet file into a pandas DataFrame

In [2]:
from pytorch_forecasting.data.examples import get_stallion_data

data = get_stallion_data()

In [3]:
data.head()

agency     sku    volume       date  industry_volume  soda_volume  \
0    Agency_22  SKU_01   52.2720 2013-01-01        492612703    718394219   
238  Agency_37  SKU_04    0.0000 2013-01-01        492612703    718394219   
237  Agency_59  SKU_03  812.9214 2013-01-01        492612703    718394219   
236  Agency_11  SKU_01  316.4400 2013-01-01        492612703    718394219   
235  Agency_05  SKU_05  420.9093 2013-01-01        492612703    718394219   

     avg_max_temp  price_regular  price_actual    discount  \
0       25.845238    1168.903668   1069.166193   99.737475   
238     26.505000    1852.273642   1611.466298  240.807344   
237     22.219737    1270.795012   1197.184260   73.610752   
236     25.360000    1176.155397   1082.757488   93.397909   
235     24.079012    1327.003396   1207.822992  119.180404   

     avg_population_2017  avg_yearly_household_income_2017  easter_day  \
0                  48151                            132110           0   
238                32769                             96761           0   
237              1219986                            218902           0   
236               135561                            100461           0   
235              3044268                            182944           0   

     good_friday  new_year  christmas  labor_day  independence_day  \
0              0         1          0          0                 0   
238            0         1          0          0                 0   
237            0         1          0          0                 0   
236            0         1          0          0                 0   
235            0         1          0          0                 0   

     revolution_day_memorial  regional_games  fifa_u_17_world_cup  \
0                          0               0                    0   
238                        0               0                    0   
237                        0               0                    0   
236                        0               0                    0   
235                        0               0                    0   

     football_gold_cup  beer_capital  music_fest  discount_in_percent  \
0                    0             0           0             8.532566   
238                  0             0           0            13.000635   
237                  0             0           0             5.792496   
236                  0             0           0             7.940950   
235                  0             0           0             8.981168   

     timeseries  
0             0  
238           5  
237           9  
236          14  
235          22

add time index

In [4]:
data["time_idx"] = data["date"].dt.year * 12 + data["date"].dt.month
data["time_idx"] -= data["time_idx"].min()

add additional features

In [5]:
data["month"] = data.date.dt.month.astype(str).astype("category")  # categories have be strings
data["log_volume"] = np.log(data.volume + 1e-8)
data["avg_volume_by_sku"] = data.groupby(["time_idx", "sku"], observed=True).volume.transform("mean")
data["avg_volume_by_agency"] = data.groupby(["time_idx", "agency"], observed=True).volume.transform("mean")

we want to encode special days as one variable and thus need to first reverse one-hot encoding

In [6]:
special_days = [
    "easter_day",
    "good_friday",
    "new_year",
    "christmas",
    "labor_day",
    "independence_day",
    "revolution_day_memorial",
    "regional_games",
    "fifa_u_17_world_cup",
    "football_gold_cup",
    "beer_capital",
    "music_fest",
]
data[special_days] = data[special_days].apply(lambda x: x.map({0: "-", 1: x.name})).astype("category")
data.sample(10, random_state=521)

agency     sku     volume       date  industry_volume  soda_volume  \
291    Agency_25  SKU_03     0.5076 2013-01-01        492612703    718394219   
871    Agency_29  SKU_02     8.7480 2015-01-01        498567142    762225057   
19532  Agency_47  SKU_01     4.9680 2013-09-01        454252482    789624076   
2089   Agency_53  SKU_07    21.6825 2013-10-01        480693900    791658684   
9755   Agency_17  SKU_02   960.5520 2015-03-01        515468092    871204688   
7561   Agency_05  SKU_03  1184.6535 2014-02-01        425528909    734443953   
19204  Agency_11  SKU_05     5.5593 2017-08-01        623319783   1049868815   
8781   Agency_48  SKU_04  4275.1605 2013-03-01        509281531    892192092   
2540   Agency_07  SKU_21     0.0000 2015-10-01        544203593    761469815   
12084  Agency_21  SKU_03    46.3608 2017-04-01        589969396    940912941   

       avg_max_temp  price_regular  price_actual    discount  \
291       25.845238    1264.162234   1152.473405  111.688829   
871       27.584615    1316.098485   1296.804924   19.293561   
19532     30.665957    1269.250000   1266.490490    2.759510   
2089      29.197727    1193.842373   1128.124395   65.717978   
9755      23.608120    1338.334248   1232.128069  106.206179   
7561      28.668254    1369.556376   1161.135214  208.421162   
19204     31.915385    1922.486644   1651.307674  271.178970   
8781      26.767857    1761.258209   1546.059670  215.198539   
2540      28.987755       0.000000      0.000000    0.000000   
12084     32.478910    1675.922116   1413.571789  262.350327   

       avg_population_2017  avg_yearly_household_income_2017  easter_day  \
291                  53598                             95032           -   
871                  28329                             93614           -   
19532                32183                            128574           -   
2089               1729177                            111048           -   
9755                147910                            123013           -   
7561               3044268                            182944           -   
19204               135561                            100461           -   
8781               1739969                            210213  easter_day   
2540               1868030                            175785           -   
12084                26635                            130092  easter_day   

       good_friday  new_year christmas labor_day  independence_day  \
291              -  new_year         -         -                 -   
871              -  new_year         -         -                 -   
19532            -         -         -         -  independence_day   
2089             -         -         -         -                 -   
9755             -         -         -         -                 -   
7561             -         -         -         -                 -   
19204            -         -         -         -                 -   
8781   good_friday         -         -         -                 -   
2540             -         -         -         -                 -   
12084  good_friday         -         -         -                 -   

      revolution_day_memorial regional_games fifa_u_17_world_cup  \
291                         -              -                   -   
871                         -              -                   -   
19532                       -              -                   -   
2089                        -              -                   -   
9755                        -              -                   -   
7561                        -              -                   -   
19204                       -              -                   -   
8781                        -              -                   -   
2540                        -              -                   -   
12084                       -              -                   -   

      football_gold_cup  beer_capital  music_fest  discount_in_perc

In [7]:
def summarize_categoricals(df, show_levels=False):
    """
        Display uniqueness in each column
    """
    data = [[df[c].unique(), len(df[c].unique()), df[c].isnull().sum()] for c in df.columns]
    df_temp = pd.DataFrame(data, index=df.columns,
                           columns=['Levels', 'No. of Levels', 'No. of Missing Values'])
    return df_temp.iloc[:, 0 if show_levels else 1:]

In [8]:
summarize_categoricals(data[['agency','sku','easter_day','timeseries','month']], show_levels=True)

Levels  No. of Levels  \
agency      ['Agency_22', 'Agency_37', 'Agency_59', 'Agenc...             58   
sku         ['SKU_01', 'SKU_04', 'SKU_03', 'SKU_05', 'SKU_...             25   
easter_day  ['-', 'easter_day']
Categories (2, object): ['...              2   
timeseries  [0, 5, 9, 14, 22, 32, 23, 37, 44, 18, 50, 58, ...            350   
month       ['1', '2', '3', '4', '5', ..., '8', '9', '10',...             12   

            No. of Missing Values  
agency                          0  
sku                             0  
easter_day                      0  
timeseries                      0  
month                           0

In [9]:
data.describe().T

count                 mean  \
volume                            21000.0          1492.403982   
date                                21000  2015-06-16 20:48:00   
industry_volume                   21000.0     543921415.616667   
soda_volume                       21000.0     851200017.016667   
avg_max_temp                      21000.0            28.612404   
price_regular                     21000.0          1451.536344   
price_actual                      21000.0           1267.34745   
discount                          21000.0           184.374146   
avg_population_2017               21000.0       1045064.568571   
avg_yearly_household_income_2017  21000.0        151073.494286   
discount_in_percent               21000.0            10.574884   
timeseries                        21000.0                174.5   
time_idx                          21000.0                 29.5   
log_volume                        21000.0             2.464118   
avg_volume_by_sku                 21000.0          1492.403982   
avg_volume_by_agency              21000.0          1492.403982   

                                                  min                  25%  \
volume                                            0.0             8.272388   
date                              2013-01-01 00:00:00  2014-03-24 06:00:00   
industry_volume                           413051813.0          509055292.5   
soda_volume                               696401477.0          789088000.5   
avg_max_temp                                16.731034            25.374816   
price_regular                                     0.0          1311.547158   
price_actual                             -3121.690141          1178.365653   
discount                                          0.0            54.935108   
avg_population_2017                           12271.0              60189.0   
avg_yearly_household_income_2017              90240.0             110057.0   
discount_in_percent                               0.0             3.749628   
timeseries                                        0.0                 87.0   
time_idx                                          0.0                14.75   
log_volume                                 -18.420681             2.112923   
avg_volume_by_sku                                 0.0           932.285496   
avg_volume_by_agency                              0.0            113.42025   

                                                  50%                  75%  \
volume                                        158.436          1774.793475   
date                              2015-06-16 00:00:00  2016-09-08 12:00:00   
industry_volume                           551199995.5         589371547.75   
soda_volume                               864919588.0          900555088.0   
avg_max_temp                                28.479272            31.568405   
price_regular                             1495.174592           1725.65208   
price_actual                              1324.695705          1517.311427   
discount                                   138.307225            272.29863   
avg_population_2017                         1232242.0            1729177.0   
avg_yearly_household_income_2017             131411.0             206553.0   
discount_in_percent                           8.94899            15.647058   
timeseries                                      174.5                262.0   
time_idx                                         29.5                44.25   
log_volume                                   5.065351             7.481439   
avg_volume_by_sku                         1402.305264          2195.362302   
avg_volume_by_agency                      1730.529771            2595.3165   

                                                  max              std  
volume                                       22526.61      2711.496882  
date                              2017-12-01 00:00:00              NaN  
industry_volume                         

In [10]:
filter_data = data[(data['agency']=='Agency_57') & (data['sku']=='SKU_03')].sort_values(by='time_idx')
filter_data.head() # Luôn đủ time idx cho agency và SKU không có mising values

agency     sku      volume       date  industry_volume  soda_volume  \
232    Agency_57  SKU_03   782.12700 2013-01-01        492612703    718394219   
7284   Agency_57  SKU_03   801.58500 2013-02-01        431937346    753938444   
8968   Agency_57  SKU_03   866.98050 2013-03-01        509281531    892192092   
10811  Agency_57  SKU_03  1307.40825 2013-04-01        532390389    838099501   
12540  Agency_57  SKU_03  1020.44550 2013-05-01        551755254    864420003   

       avg_max_temp  price_regular  price_actual    discount  \
232       22.219737    1268.558431   1165.031186  103.527245   
7284      25.637500    1267.149338   1158.123783  109.025555   
8968      24.925652    1285.234686   1177.612551  107.622135   
10811     27.930736    1312.239461   1129.051331  183.188130   
12540     27.555022    1318.155168   1122.874614  195.280554   

       avg_population_2017  avg_yearly_household_income_2017  easter_day  \
232                2212416                            187351           -   
7284               2212416                            187351           -   
8968               2212416                            187351  easter_day   
10811              2212416                            187351           -   
12540              2212416                            187351           -   

       good_friday  new_year christmas  labor_day independence_day  \
232              -  new_year         -          -                -   
7284             -         -         -          -                -   
8968   good_friday         -         -          -                -   
10811            -         -         -          -                -   
12540            -         -         -  labor_day                -   

      revolution_day_memorial regional_games fifa_u_17_world_cup  \
232                         -              -                   -   
7284                        -              -                   -   
8968                        -              -                   -   
10811                       -              -                   -   
12540                       -              -                   -   

      football_gold_cup beer_capital  music_fest  discount_in_percent  \
232                   -            -           -             8.161015   
7284                  -            -           -             8.604002   
8968                  -            -  music_fest             8.373734   
10811                 -            -           -            13.959962   
12540                 -            -           -            14.814686   

       timeseries  time_idx month  log_volume  avg_volume_by_sku  \
232            37         0     1    6.662017        1225.306376   
7284           37         1     2    6.686591        1289.885997   
8968           37         2     3    6.765016        1432.225016   
10811          37         3     4    7.175802        1564.910937   
12540          37         4     5    6.927995        1741.896147   

       avg_volume_by_agency  
232             1821.292500  
7284            1963.349531  
8968            2162.780156  
10811           2433.855281  
12540           2385.850219

In [11]:
data.info()

<class 'pandas.core.frame.DataFrame'>
Index: 21000 entries, 0 to 6650
Data columns (total 31 columns):
 #   Column                            Non-Null Count  Dtype         
---  ------                            --------------  -----         
 0   agency                            21000 non-null  category      
 1   sku                               21000 non-null  category      
 2   volume                            21000 non-null  float64       
 3   date                              21000 non-null  datetime64[ns]
 4   industry_volume                   21000 non-null  int64         
 5   soda_volume                       21000 non-null  int64         
 6   avg_max_temp                      21000 non-null  float64       
 7   price_regular                     21000 non-null  float64       
 8   price_actual                      21000 non-null  float64       
 9   discount                          21000 non-null  float64       
 10  avg_population_2017               21000 non-null  in

In [12]:
data.head()

agency     sku    volume       date  industry_volume  soda_volume  \
0    Agency_22  SKU_01   52.2720 2013-01-01        492612703    718394219   
238  Agency_37  SKU_04    0.0000 2013-01-01        492612703    718394219   
237  Agency_59  SKU_03  812.9214 2013-01-01        492612703    718394219   
236  Agency_11  SKU_01  316.4400 2013-01-01        492612703    718394219   
235  Agency_05  SKU_05  420.9093 2013-01-01        492612703    718394219   

     avg_max_temp  price_regular  price_actual    discount  \
0       25.845238    1168.903668   1069.166193   99.737475   
238     26.505000    1852.273642   1611.466298  240.807344   
237     22.219737    1270.795012   1197.184260   73.610752   
236     25.360000    1176.155397   1082.757488   93.397909   
235     24.079012    1327.003396   1207.822992  119.180404   

     avg_population_2017  avg_yearly_household_income_2017 easter_day  \
0                  48151                            132110          -   
238                32769                             96761          -   
237              1219986                            218902          -   
236               135561                            100461          -   
235              3044268                            182944          -   

    good_friday  new_year christmas labor_day independence_day  \
0             -  new_year         -         -                -   
238           -  new_year         -         -                -   
237           -  new_year         -         -                -   
236           -  new_year         -         -                -   
235           -  new_year         -         -                -   

    revolution_day_memorial regional_games fifa_u_17_world_cup  \
0                         -              -                   -   
238                       -              -                   -   
237                       -              -                   -   
236                       -              -                   -   
235                       -              -                   -   

    football_gold_cup beer_capital music_fest  discount_in_percent  \
0                   -            -          -             8.532566   
238                 -            -          -            13.000635   
237                 -            -          -             5.792496   
236                 -            -          -             7.940950   
235                 -            -          -             8.981168   

     timeseries  time_idx month  log_volume  avg_volume_by_sku  \
0             0         0     1    3.956461        2613.377501   
238           5         0     1  -18.420681        1361.511918   
237           9         0     1    6.700634        1225.306376   
236          14         0     1    5.757134        2613.377501   
235          22         0     1    6.042417        1179.728165   

     avg_volume_by_agency  
0              103.805460  
238              0.549900  
237           2041.909586  
236            125.690220  
235           1638.463500

In [13]:
cate_cols = ['new_year','month']
for col in cate_cols:
    haha = NaNLabelEncoder(add_nan=True).fit_transform(data[col])
    print (f"col {col} >>> {set(np.array(haha))}" )

col new_year >>> {1, 2}
col month >>> {1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12}


In [14]:
data[cate_cols].info()

<class 'pandas.core.frame.DataFrame'>
Index: 21000 entries, 0 to 6650
Data columns (total 2 columns):
 #   Column    Non-Null Count  Dtype   
---  ------    --------------  -----   
 0   new_year  21000 non-null  category
 1   month     21000 non-null  category
dtypes: category(2)
memory usage: 205.6 KB


In [ ]:
max_prediction_length = 6
max_encoder_length = 24
training_cutoff = data["time_idx"].max() - max_prediction_length

## Create Dataset

In [ ]:
training = TimeSeriesDataSet(
    data[lambda x: x.time_idx <= training_cutoff],
    time_idx="time_idx",
    target=["volume","month"],
    group_ids=["agency", "sku"],
    min_encoder_length=max_encoder_length // 2,  # keep encoder length long (as it is in the validation set)
    max_encoder_length=max_encoder_length,
    min_prediction_length=1,
    max_prediction_length=max_prediction_length,
    static_categoricals=["agency", "sku"],
    static_reals=["avg_population_2017", "avg_yearly_household_income_2017"],
    time_varying_known_categoricals=["special_days"],
    variable_groups={"special_days": special_days},  # group of categorical variables can be treated as one variable
    time_varying_known_reals=["time_idx", "price_regular", "discount_in_percent"],
    time_varying_unknown_categoricals=[],
    time_varying_unknown_reals=[
        "volume",
        "log_volume",
        "industry_volume",
        "soda_volume",
        "avg_max_temp",
        "avg_volume_by_agency",
        "avg_volume_by_sku",
    ],
    target_normalizer=MultiNormalizer(
        [EncoderNormalizer(method='standard',center=True,max_length=None,transformation=None,method_kwargs={}), 
         NaNLabelEncoder(add_nan=True, warn=True), # Use the NaNLabelEncoder to encode categorical target
        #  EncoderNormalizer(method='standard',center=True,max_length=None,transformation=None,method_kwargs={}),
         ]
    ),  
    add_relative_time_idx=True,
    add_target_scales=True,
    add_encoder_length=True,
)

In [ ]:
x, y = next(iter(training.to_dataloader(batch_size=4)))
y[0]

/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:439: U

[tensor([[ 38.1375,  40.9342,  51.6358,  62.7732,  46.6992,  36.0396],
         [323.6760, 300.7800, 532.7640, 453.8160, 456.3000, 356.8320],
         [  0.0000,   0.0000,   0.0000,   0.0000,   0.0000,   0.0000],
         [  0.9585,   0.9585,   0.0000,   1.2780,   0.6390,   0.6390]]),
 tensor([[ 1,  5,  6,  7,  8,  9],
         [ 8,  9, 10, 11, 12,  2],
         [ 7,  8,  9, 10, 11, 12],
         [10, 11, 12,  2,  3,  4]])]

In [ ]:
training.target_normalizers

[EncoderNormalizer(
 	method='standard',
 	center=True,
 	max_length=None,
 	transformation=None,
 	method_kwargs={}
 ),
 NaNLabelEncoder(add_nan=True, warn=True)]

In [ ]:
training.dropout_categoricals

[]

In [ ]:
# create validation set (predict=True) which means to predict the last max_prediction_length points in time for each series
validation = TimeSeriesDataSet.from_dataset(training, data, predict=True, stop_randomization=True)
# create dataloaders for model
batch_size = 128  # set this between 32 to 128
train_dataloader = training.to_dataloader(train=True, batch_size=batch_size, num_workers=0)
val_dataloader = validation.to_dataloader(train=False, batch_size=batch_size * 10, num_workers=0)

## configure network and trainer

In [ ]:
random_seed = 42

In [ ]:
pl.seed_everything(random_seed)
trainer = pl.Trainer(
    accelerator="cpu",
    # clipping gradients is a hyperparameter and important to prevent divergance
    # of the gradient for recurrent neural networks
    gradient_clip_val=0.1,
)

Global seed set to 42
GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs


In [ ]:
tft = TemporalFusionTransformer.from_dataset(
    training,
    learning_rate=0.03,
    hidden_size=16,
    attention_head_size=1,
    dropout=0.1,
    hidden_continuous_size=8,
    output_size=[7,13],  # 7 quantiles by default, 3 outputs for Multi-Target. Classification = num_classes + 1
    loss=MultiLoss([QuantileLoss(),CrossEntropy()]), # using MultiLoss for Multi-Target regression/classification
    log_interval=10,  # uncomment for learning rate finder and otherwise, e.g. to 10 for logging every 10 batches
    reduce_on_plateau_patience=4,
)
print(f"Number of parameters in network: {tft.size()/1e3:.1f}k")

Number of parameters in network: 29.3k


/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/lightning/pytorch/utilities/parsing.py:196: UserWarning: Attribute 'loss' is an instance of `nn.Module` and is already saved during checkpointing. It is recommended to ignore them using `self.save_hyperparameters(ignore=['loss'])`.
  rank_zero_warn(
/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/lightning/pytorch/utilities/parsing.py:196: UserWarning: Attribute 'logging_metrics' is an instance of `nn.Module` and is already saved during checkpointing. It is recommended to ignore them using `self.save_hyperparameters(ignore=['logging_metrics'])`.
  rank_zero_warn(


In [ ]:
# tft.hparams

find optimal learning rate

In [ ]:
from lightning.pytorch.tuner import Tuner

In [ ]:
res = Tuner(trainer).lr_find( 
    tft,
    train_dataloaders=train_dataloader,
    val_dataloaders=val_dataloader,
    max_lr=10.0,
    min_lr=1e-6,
) 

/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/lightning/pytorch/loops/utilities.py:70: PossibleUserWarning: `max_epochs` was not set. Setting it to 1000 epochs. To train without an epoch limit, set `max_epochs=-1`.
  rank_zero_warn(
Missing logger folder: /workspaces/multiple_time_series_multitask_learning/lightning_logs
/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but StandardScaler was fitted with

/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/pytorch_forecasting/models/temporal_fusion_transformer/__init__.py:735: UserWarning: The figure layout has changed to tight
  f.tight_layout()
/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:

Finding best initial lr:   0%|          | 0/100 [00:00<?, ?it/s]

/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:439: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:439: U

: 

: 

In [ ]:
print(f"suggested learning rate: {res.suggestion()}")
fig = res.plot(show=True, suggest=True)
fig.show()

NameError: name 'res' is not defined

## Training

In [ ]:
early_stop_callback = EarlyStopping(monitor="val_loss", min_delta=1e-4, patience=10, verbose=False, mode="min")
lr_logger = LearningRateMonitor()  # log the learning rate
logger = TensorBoardLogger("lightning_logs_test")  # logging results to a tensorboard

In [ ]:
trainer = pl.Trainer(
    max_epochs=2,
    accelerator="cpu",
    enable_model_summary=True,
    gradient_clip_val=0.1,
    limit_train_batches=50,  # coment in for training, running valiation every 30 batches
    # fast_dev_run=True,  # comment in to check that networkor dataset has no serious bugs
    callbacks=[lr_logger, early_stop_callback],
    logger=logger,
)

GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs


In [ ]:
tft = TemporalFusionTransformer.from_dataset(
    training,
    learning_rate=0.03,
    hidden_size=16,
    attention_head_size=1,
    dropout=0.1,
    hidden_continuous_size=8,
    output_size=[7,13],  # 7 quantiles by default, two outputs for Multi-Target
    # loss=MultiLoss([QuantileLoss(),QuantileLoss()]), # using MultiLoss for Multi-Target regression/regression
    loss=MultiLoss([QuantileLoss(),CrossEntropy()]), # using MultiLoss for Multi-Target regression/classification
    log_interval=10,  # uncomment for learning rate finder and otherwise, e.g. to 10 for logging every 10 batches
    reduce_on_plateau_patience=4,
)
print(f"Number of parameters in network: {tft.size()/1e3:.1f}k")

Number of parameters in network: 29.3k


/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/lightning/pytorch/utilities/parsing.py:197: UserWarning: Attribute 'loss' is an instance of `nn.Module` and is already saved during checkpointing. It is recommended to ignore them using `self.save_hyperparameters(ignore=['loss'])`.
  rank_zero_warn(
/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/lightning/pytorch/utilities/parsing.py:197: UserWarning: Attribute 'logging_metrics' is an instance of `nn.Module` and is already saved during checkpointing. It is recommended to ignore them using `self.save_hyperparameters(ignore=['logging_metrics'])`.
  rank_zero_warn(


In [ ]:
trainer.fit(
    tft,
    train_dataloaders=train_dataloader,
    val_dataloaders=val_dataloader,
)

Missing logger folder: lightning_logs_test/lightning_logs

   | Name                               | Type                            | Params
----------------------------------------------------------------------------------------
0  | loss                               | MultiLoss                       | 0     
1  | logging_metrics                    | ModuleList                      | 0     
2  | input_embeddings                   | MultiEmbedding                  | 1.2 K 
3  | prescalers                         | ModuleDict                      | 256   
4  | static_variable_selection          | VariableSelectionNetwork        | 3.4 K 
5  | encoder_variable_selection         | VariableSelectionNetwork        | 7.7 K 
6  | decoder_variable_selection         | VariableSelectionNetwork        | 2.6 K 
7  | static_context_variable_selection  | GatedResidualNetwork            | 1.1 K 
8  | static_context_initial_hidden_lstm | GatedResidualNetwork            | 1.1 K 
9  | static_context_in

Sanity Checking: 0it [00:00, ?it/s]

/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:464: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:464: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:464: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:464: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:464: U

Sanity Checking DataLoader 0:   0%|          | 0/1 [00:00<?, ?it/s]

/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:464: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:464: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:464: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:464: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:464: U

...

/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:464: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:464: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:464: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:464: UserWarning: X does not have valid feature names, but StandardScaler was fitted with feature names
  warnings.warn(
/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/sklearn/base.py:464: U

Epoch 0:  96%|█████████▌| 48/50 [00:18<00:00,  2.55it/s, v_num=0, train_loss_step=158.0]

SIGTERMException: 

/workspaces/multiple_time_series_multitask_learning/venv/lib/python3.10/site-packages/IPython/core/interactiveshell.py:3516: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)


: 

This is to load the model you want

In [ ]:
best_model_path = 'lightning_logs_test/lightning_logs/version_0/checkpoints/epoch=1-step=6.ckpt' # Classification
best_tft = TemporalFusionTransformer.load_from_checkpoint(best_model_path)

%%<br>
calcualte root mean squared error on validation set

In [ ]:
actuals = [y[0] for x, y in iter(val_dataloader)]
val_predictions = tft.predict(val_dataloader)

%%

In [ ]:
actuals[0]

%%

In [ ]:
val_predictions